In [1]:
import numpy as np
import scipy
from clock_project.simulation.magnitude_quantification import calculate_information
import scipy
import json
from cogent3.util.deserialise import deserialise_object
import numpy as np
import os
import glob

import plotly.express as px
from cogent3.maths.measure import jsd
from cogent3 import get_app, open_data_store



In [2]:
from scipy.stats import spearmanr

In [4]:
# alignment_length = json.load(open('/Users/gulugulu/repos/PuningAnalysis/results/output_data/genome_information/alignment_lengths_550_threshold.json', 'r'))
# number_of_species = json.load(open('/Users/gulugulu/repos/PuningAnalysis/results/output_data/genome_information/sample_sizes_full.json', 'r'))
# alignment_length_list = [int(alignment_length[gene]) for gene in alignment_length]
# number_of_species_list = [int(number_of_species[gene]) for gene in alignment_length]

In [5]:
# # Create the histogram with density normalization
# fig = px.histogram(
#     alignment_length_list,
#     labels={'x': 'Alignment Length (3rd codon position)', 'y': 'Density'},
#     title=None,
#     color_discrete_sequence=['#acd1be'],  # Set the color to a shade of orange
#     histnorm='percent'  # Normalize the histogram to density
# )   

# # Update layout for presentation
# fig.update_layout(
#     template='plotly_white',
#     margin=dict(l=50, r=50, t=50, b=50),  # Adjust margins for a balanced look
#     autosize=True,
#     yaxis_title='<b>Count</b>',  # Explicit y-axis title
#     xaxis_title='<b>Alignment Length (3rd codon position)</b>',  # Explicit x-axis title
#     yaxis_title_font=dict(size=20),  # Adjust y-axis font size
#     xaxis_title_font=dict(size=20),  # Adjust x-axis font size
#     font=dict(size=16),  # General font size for labels and titles
#     width=600,  # Set figure width (optional for better control)
#     height=500,  # Set figure height (optional for better control)
#     showlegend=False  # Remove the legend
# )

# # Set transparency level and add a solid line around each bar
# fig.update_traces(
#     opacity=0.8,  # Set the transparency (0 = fully transparent, 1 = fully opaque)
#     marker_line_color='black',  # Color of the line around each bar
#     marker_line_width=1.5  # Width of the line around each bar
# )

# fig.update_xaxes(range=[470, 2900])
# fig.update_yaxes(range=[0, 35])

# fig.write_image('alignment_length_histogram.pdf')
# fig.show()

In [6]:
# # Create the histogram with density normalization
# fig = px.histogram(
#     number_of_species_list,
#     labels={'x': 'Number of Species', 'y': 'Density'},
#     title=None,
#     color_discrete_sequence=['#acd1be'],  # Set the color to a shade of orange
#     histnorm='density'  # Normalize the histogram to density
# )   

# # Update layout for presentation
# fig.update_layout(
#     template='plotly_white',
#     margin=dict(l=50, r=50, t=50, b=50),  # Adjust margins for a balanced look
#     autosize=True,
#     yaxis_title='<b>Count</b>',  # Explicit y-axis title
#     xaxis_title='<b>Number of Species</b>',  # Explicit x-axis title
#     yaxis_title_font=dict(size=20),  # Adjust y-axis font size
#     xaxis_title_font=dict(size=20),  # Adjust x-axis font size
#     font=dict(size=16),  # General font size for labels and titles
#     width=600,  # Set figure width (optional for better control)
#     height=500,  # Set figure height (optional for better control)
#     showlegend=False  # Remove the legend
# )

# # Set transparency level and add a solid line around each bar
# fig.update_traces(
#     opacity=0.8,  # Set the transparency (0 = fully transparent, 1 = fully opaque)
#     marker_line_color='black',  # Color of the line around each bar
#     marker_line_width=1.5  # Width of the line around each bar
# )

# fig.update_xaxes(range=[31, 66])

# # fig.write_image('number_of_species_histogram.pdf')
# fig.show()

In [ ]:
# import statistics
# def get_summary_statistics(data):
#     if len(data) == 0:
#         return "List is empty."
    
#     summary_stats = {
#         "mean": statistics.mean(data),
#         "median": statistics.median(data),
#         "variance": statistics.variance(data),
#         "standard_deviation": statistics.stdev(data),
#         "min": min(data),
#         "max": max(data),
#         "sum": sum(data),
#         "count": len(data)
#     }
    
#     return summary_stats

# summary_stats_aln_len_550 = get_summary_statistics(alignment_length_list)
# summary_stats_species_num_550 = get_summary_statistics(number_of_species_list)

In [28]:
def get_ingroup_names(triads_info):
    ingroup_names_dict = {}
    for identifier, info in triads_info.items():
        triads_names = info['triples_species_names']
        ingroup_names_dict[identifier] = [triads_names['ingroup1'], triads_names['ingroup2']]
    return ingroup_names_dict

In [29]:
def get_jsd_diff(triads_info):
    jsd_diff_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        nuc_freqs_dict = triads_info_value['nuc_freqs_dict']
        nuc_freq1 = nuc_freqs_dict['ingroup1']
        nuc_freq2 = nuc_freqs_dict['ingroup2']
        nuc_freq_internal_node = nuc_freqs_dict["internal_node"]
        jsd1 = jsd(nuc_freq1, nuc_freq_internal_node)
        jsd2 = jsd(nuc_freq2, nuc_freq_internal_node)
        jsd_diff = abs(jsd1 - jsd2)
        jsd_diff_dict[identifier] = jsd_diff
    return jsd_diff_dict

def get_jsd(triads_info):
    jsd_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        nuc_freqs_dict = triads_info_value['nuc_freqs_dict']
        nuc_freq1 = nuc_freqs_dict['ingroup1']
        nuc_freq2 = nuc_freqs_dict['ingroup2']
        nuc_freq_internal_node = nuc_freqs_dict["internal_node"]
        jsd1 = jsd(nuc_freq1, nuc_freq_internal_node)
        jsd2 = jsd(nuc_freq2, nuc_freq_internal_node)
        jsd_dict[identifier] = {'ingroup1': jsd1, 'ingroup2': jsd2}
    return jsd_dict
        

In [30]:
def get_ingroup_jsd(triads_info):
    ingroup_jsd_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        ingroup_jsd = triads_info_value['ingroup_jsd']
        ingroup_jsd_dict[identifier] = ingroup_jsd
    return ingroup_jsd_dict



In [31]:
def get_ingroup_ens_diff(triads_info):
    ens_ingroup_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        triads_names = info['triples_species_names']
        ens_dict = triads_info_value['ens']
        ens_ingroup = abs(np.log(ens_dict[triads_names['ingroup1']]/ ens_dict[triads_names['ingroup2']]))
        ens_ingroup_dict[identifier] = ens_ingroup
    return ens_ingroup_dict

In [32]:
def get_ingroup_ens_absdiff(triads_info):
    ens_ingroup_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        triads_names = info['triples_species_names']
        ens_dict = triads_info_value['ens']
        ens_ingroup = abs(ens_dict[triads_names['ingroup1']]- ens_dict[triads_names['ingroup2']])
        ens_ingroup_dict[identifier] = ens_ingroup
    return ens_ingroup_dict

def get_ens(triads_info):
    ens_value_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        triads_names = info['triples_species_names']
        ens_dict = triads_info_value['ens']
        ens1 = ens_dict[triads_names['ingroup1']]
        ens2 = ens_dict[triads_names['ingroup2']]
        ens_value_dict[identifier] = {'ingroup1': ens1, 'ingroup2': ens2}
    return ens_value_dict


In [33]:
def get_nabla_absdiff(triads_info):
    nabla_diff_dict = {}
    for identifier, info in triads_info.items():
        triads_info_value = info['triples_info_small_tree']
        triads_names = info['triples_species_names']
        nabla_dict = triads_info_value['nabla_values']
        nbala_diff = abs(nabla_dict[triads_names['ingroup1']] - nabla_dict[triads_names['ingroup2']])
        nabla_diff_dict[identifier] = nbala_diff
    return nabla_diff_dict

In [34]:
def remove_outliers_iqr(data1, data2):
    def compute_iqr_bounds(data):
        Q1 = np.percentile(data, 25)
        Q3 = np.percentile(data, 75)
        IQR = Q3 - Q1
        lower_bound = Q1 - 5 * IQR
        upper_bound = Q3 + 5 * IQR
        return lower_bound, upper_bound

    # Calculate IQR bounds for both lists
    lower_bound1, upper_bound1 = compute_iqr_bounds(data1)
    lower_bound2, upper_bound2 = compute_iqr_bounds(data2)

    # Filter out pairs where either value is an outlier
    filtered_data1 = []
    filtered_data2 = []

    for val1, val2 in zip(data1, data2):
        if (lower_bound1 <= val1 <= upper_bound1) and (lower_bound2 <= val2 <= upper_bound2):
            filtered_data1.append(val1)
            filtered_data2.append(val2)

    return filtered_data1, filtered_data2

In [35]:
import os
import json
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Function to load JSON data
def load_json_data(path):
    with open(path, 'r') as file:
        return json.load(file)

In [36]:
import os

triples_model_fitting_dir = '/Users/gulugulu/clock/mammal_orthologs_hsap_1/triples_model_fitting'
gene_paths = glob.glob(os.path.join(triples_model_fitting_dir, '*/'))

species_names = {}
for path in gene_paths:
    gene_name = os.path.basename(path.rstrip('/'))
    triads_data_path = os.path.join(path, 'triples_info_dict_new.json')
    triads_info = load_json_data(triads_data_path)
    ingroup_names = get_ingroup_names(triads_info)
    species_names[gene_name] = ingroup_names

repeated_names_dict = {}
for gene, species in species_names.items():
    repeated_names_dict[gene] = []  # Initialize a list to store pairs
    for identifier, ingroup in species.items():
        for identifier2, ingroup2 in species.items():
            if identifier < identifier2:  # Ensure each pair is only processed once
                if ingroup == ingroup2:
                    repeated_names_dict[gene].append((identifier, identifier2))

# Optional: Remove genes with no repeated pairs
repeated_names_dict = {gene: pairs for gene, pairs in repeated_names_dict.items() if pairs}


In [37]:
removed_identifier = {gene: [a[0] for a in repeated_names_dict[gene]] if gene in repeated_names_dict else [] for gene in species_names}

In [38]:
removed_identifier

{'ENSG00000137962': ['246'],
 'ENSG00000116675': ['101', '38'],
 'ENSG00000163873': ['229'],
 'ENSG00000122482': ['40'],
 'ENSG00000116688': ['105'],
 'ENSG00000149527': ['142', '125', '201', '165', '183'],
 'ENSG00000122218': [],
 'ENSG00000054523': ['195'],
 'ENSG00000152104': ['180', '196', '236', '14'],
 'ENSG00000177888': [],
 'ENSG00000117707': ['153'],
 'ENSG00000122483': ['31', '218', '13', '265'],
 'ENSG00000027644': [],
 'ENSG00000136643': ['231'],
 'ENSG00000085999': ['191'],
 'ENSG00000197147': [],
 'ENSG00000059588': ['20', '235'],
 'ENSG00000058668': ['117'],
 'ENSG00000162687': [],
 'ENSG00000116991': ['250'],
 'ENSG00000066135': ['169', '234', '147'],
 'ENSG00000143569': ['149', '198'],
 'ENSG00000116337': ['30', '184', '126'],
 'ENSG00000085998': [],
 'ENSG00000163399': [],
 'ENSG00000162688': [],
 'ENSG00000171608': ['218', '106', '156'],
 'ENSG00000135775': ['138'],
 'ENSG00000117425': ['169', '153'],
 'ENSG00000133216': ['123', '179'],
 'ENSG00000198734': ['271', '2

In [18]:
def get_names(triads_info):
    names_dict = {}
    for identifier, info in triads_info.items():
        triads_names = info['triples_species_names']
        names_dict[identifier] = triads_names
    return names_dict

In [39]:
# Function to compute required values
def compute_values(path):
    gene_name = os.path.basename(path.rstrip('/'))

    triads_data_path = os.path.join(path, 'triples_info_dict_new.json')
    triads_info_original = load_json_data(triads_data_path)
    triads_info = {k: v for k, v in triads_info_original.items() if k not in removed_identifier[gene_name]}
    ens_abs_diff_dict = get_ingroup_ens_absdiff(triads_info)
    jsd_diff_dict = get_jsd_diff(triads_info)
    ens_dict = get_ens(triads_info)
    jsd_dict = get_jsd(triads_info)
    ingroup_jsd_dict = get_ingroup_jsd(triads_info)
    nabla_absdiff_dict = get_nabla_absdiff(triads_info)
    species_names_dict = get_names(triads_info)
    ens_abs_diff_list = list(ens_abs_diff_dict.values())
    jsd_diff_list = list(jsd_diff_dict.values())
    ingroup_jsd_list = list(ingroup_jsd_dict.values())
    nabla_absdiff_list = list(nabla_absdiff_dict.values())
    ens_list = list(ens_dict.values())
    jsd_list = list(jsd_dict.values())
    species_names_list = list(species_names_dict.values())

    

    return  ens_abs_diff_list, jsd_diff_list, ingroup_jsd_list, nabla_absdiff_list, ens_list, jsd_list, species_names_list

In [40]:
# Initialize the dictionary to store the data
gene_data_dict = {}
# Populate the dictionary with data for each gene
for path in gene_paths:
    gene_name = os.path.basename(path.rstrip('/'))
    ens_abs_diff_list, jsd_diff_list, ingroup_jsd_list, nabla_absdiff_list, ens_list, jsd_list, species_names_list = compute_values(path)
    gene_data_dict[gene_name] = {
        'ens_abs_diff': ens_abs_diff_list,
        'jsd_diff': jsd_diff_list, 
        'ingroup_jsd': ingroup_jsd_list,
        'nabla_absdiff': nabla_absdiff_list,
        'ens': ens_list,
        'jsd': jsd_list,
        'species_names': species_names_list
    }

In [41]:
number_of_triples = {gene: len(data['species_names']) for gene, data in gene_data_dict.items()}

In [42]:
number_of_triples

{'ENSG00000137962': 214,
 'ENSG00000116675': 178,
 'ENSG00000163873': 211,
 'ENSG00000122482': 149,
 'ENSG00000116688': 235,
 'ENSG00000149527': 229,
 'ENSG00000122218': 213,
 'ENSG00000054523': 216,
 'ENSG00000152104': 201,
 'ENSG00000177888': 210,
 'ENSG00000117707': 216,
 'ENSG00000122483': 214,
 'ENSG00000027644': 219,
 'ENSG00000136643': 178,
 'ENSG00000085999': 207,
 'ENSG00000197147': 201,
 'ENSG00000059588': 185,
 'ENSG00000058668': 211,
 'ENSG00000162687': 196,
 'ENSG00000116991': 209,
 'ENSG00000066135': 227,
 'ENSG00000143569': 221,
 'ENSG00000116337': 229,
 'ENSG00000085998': 224,
 'ENSG00000163399': 226,
 'ENSG00000162688': 170,
 'ENSG00000171608': 220,
 'ENSG00000135775': 207,
 'ENSG00000117425': 199,
 'ENSG00000133216': 222,
 'ENSG00000198734': 215,
 'ENSG00000121957': 175,
 'ENSG00000184144': 220,
 'ENSG00000116984': 227,
 'ENSG00000197106': 235,
 'ENSG00000143126': 218,
 'ENSG00000058085': 231,
 'ENSG00000187554': 198,
 'ENSG00000143322': 187,
 'ENSG00000143341': 221,


In [44]:
ens_a_list = []
invalid_triple_list = []
for path in gene_paths:
    gene_name = os.path.basename(path.rstrip('/'))
    triads_data_path = os.path.join(path, 'triples_info_dict_new.json')
    triads_info = load_json_data(triads_data_path)
    for identifier, info in triads_info.items():
        ens_dict = info['triples_info_small_tree']['ens']
        for value in ens_dict.values():
            ens_a_list.append(value)
            if value > 1:
                invalid_triple_list.append((gene_name, identifier))

invalid_triple_list
    

[]

Does species with higher JAD also evolve faster? 

In [45]:
correlation_list = []
p_value_list= []
for gene, lists in gene_data_dict.items():
    ens_list = []
    jad_list = []
    for ens in lists['ens']:
        ens_list.extend(list(ens.values()))
    for jad in lists['jsd']:
        jad_list.extend(list(jad.values()))
    #Add the correlation factor in the list
    cor, p_value = scipy.stats.spearmanr(ens_list, jad_list)
    correlation_list.append(cor)
    p_value_list.append(p_value)

In [ ]:
import plotly.graph_objects as go
gene_names = list(gene_data_dict.keys())
# Define color based on p-value condition
colors = ['blue' if p < 0.05 else 'red' for p in p_value_list]

# Create the bar plot
fig = go.Figure(go.Bar(
    x=correlation_list,
    y=gene_names,
    orientation='h',  # Horizontal bar chart
    marker=dict(color=colors),  # Color based on p-value threshold
))

# Update layout for better visualization
fig.update_layout(
    xaxis_title="Correlation Coefficient",
    yaxis_title="Gene ID",
    height=1200,  # Adjust height based on the number of genes to avoid squeezing
    yaxis=dict(showticklabels=False),  # Hide y-axis tick labels (gene names still appear)
)


In [45]:
ens_sum_list = []
for a in gene_data_dict['ENSG00000151461']['ens']:
    ens_sum_list.extend(list(a.values()))

jad_sum_list = []
for a in gene_data_dict['ENSG00000151461']['jsd']:
    jad_sum_list.extend(list(a.values()))

cor, p_value = scipy.stats.spearmanr(ens_sum_list, jad_sum_list)

import plotly.express as px
no_outliers_jad, no_outliers_ens = remove_outliers_iqr(jad_sum_list, ens_sum_list)
fig = px.scatter(x = no_outliers_jad, y = no_outliers_ens, labels={'x':'jad', 'y':'ens'}, title= None)
# Update layout with labels and title
fig.update_layout(
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    autosize=True,
    yaxis_title_font={'size': 20},  
    xaxis_title_font={'size': 20}, 
    width=None 
)
fig.show()

Pearson Correlation Test Nabla Abs Diff Vs. ENS Abs Diff

In [47]:

correlation_list0 = []
p_value_list0 = []
for gene, lists in gene_data_dict.items():
    nabla_absdiff_list, ens_abs_diff_list = remove_outliers_iqr(lists['nabla_absdiff'], lists['ens_abs_diff'])
    #Add the correlation factor in the list
    cor, p_value = scipy.stats.spearmanr(np.abs(list(nabla_absdiff_list)), np.abs(list(ens_abs_diff_list)))
    correlation_list0.append(cor)
    p_value_list0.append(p_value)

fig0 = px.box(correlation_list0, title= 'Pearson Correlation Test Nabla Abs Diff Vs. ENS Abs Diff')
# Update layout with labels and title
fig0.update_layout(
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    autosize=True,
    yaxis_title_font={'size': 20},  
    xaxis_title_font={'size': 20}, 
    xaxis_title='Correlation Coefficient',
    yaxis_title='Value',
    width=None
)
fig0.show()
# fig1.write_image('nabla_ens_cc.pdf')

Pearson Correlation Test In-group JSD Vs. ENS difference

In [48]:
correlation_list4 = {}
p_value_list4 = {}
for gene, lists in gene_data_dict.items():
    ingroup_jsd_list, ens_abs_diff_list = remove_outliers_iqr(lists['ingroup_jsd'], lists['ens_abs_diff'])

    #Add the correlation factor in the list
    cor, p_value = scipy.stats.spearmanr(ingroup_jsd_list, ens_abs_diff_list)
    correlation_list4[gene] = cor
    p_value_list4[gene] = p_value 

fig3 = px.box(correlation_list4.values(), title= 'Pearson Correlation Test In-group JSD Vs. ENS difference')
# Update layout with labels and title
fig3.update_layout(
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    autosize=True,
    yaxis_title_font={'size': 20},  
    xaxis_title_font={'size': 20}, 
    xaxis_title='Correlation Coefficient',
    yaxis_title='Value',
    width=None
)
fig3.show()
# fig2.write_image('jsd_ens_diff_cc.pdf')



In [49]:
len([i for i in p_value_list4.keys() if p_value_list4[i] < 0.05 and correlation_list4[i] > 0.2])

107

# Spearman Correlation Test JAD Difference Vs. ENS difference

In [50]:
import pandas as pd
species_number_dict = {}
max_group_size_dict = {}
num_group_dict = {}

for gene, value in gene_data_dict.items():
    data_f = pd.DataFrame({
        'ens_abs_diff': np.sqrt(value['ens_abs_diff']),
        'jsd_diff': np.sqrt(value['jsd_diff']),
        'Species1': [x['ingroup1'] for x in value['species_names']],
        'Species2': [x['ingroup2'] for x in value['species_names']],
        'Species3': [x['outgroup'] for x in value['species_names']]
    })

    data_long = pd.melt(
        data_f,
        id_vars=['ens_abs_diff', 'jsd_diff'],
        value_vars=['Species1', 'Species2', 'Species3'],
        var_name='Species_Position',
        value_name='Species'
    )
    data_long['ens_abs_diff'] = data_long['ens_abs_diff']
    data_long['jsd_diff'] = data_long['jsd_diff']
    data_long['Species'] = data_long['Species'].astype(str)
    data_long['Species'] = data_long['Species'].astype('category')

    num_groups = len(set(data_long['Species']))
    species_number_dict[gene] = len(set(data_long['Species']))
    num_group_dict[gene] = num_groups
    max_group_size = max(data_long.groupby('Species').size())
    max_group_size_dict[gene] = max_group_size
    
correlation_list3 = {}
p_value_list3 = {}
for gene, lists in gene_data_dict.items():
    jsd_diff_list, ens_abs_diff_list = remove_outliers_iqr(lists['jsd_diff'], lists['ens_abs_diff'])

    #Add the correlation factor in the list
    cor, p_value = scipy.stats.spearmanr(jsd_diff_list, ens_abs_diff_list)
    correlation_list3[gene] = cor
    p_value_list3[gene] = p_value 

# Step 1: Correct p-values using the group size
corrected_p_value_jad = {gene: p_value_list3[gene]*max_group_size_dict[gene] for gene in gene_data_dict.keys()}

significant_genes_corrected_5 = [gene for gene in gene_data_dict.keys() if corrected_p_value_jad[gene] < 0.05]
significant_genes_corrected_1 = [gene for gene in gene_data_dict.keys() if corrected_p_value_jad[gene] < 0.01]

significant_genes_correlation_dict_5 = {gene: correlation_list3[gene] for gene in significant_genes_corrected_5}
significant_genes_correlation_dict_1 = {gene: correlation_list3[gene] for gene in significant_genes_corrected_1}

# Step 2: Apply Benjamini-Hochberg procedure
# Create a DataFrame with genes and p-values
results_df1 = pd.DataFrame({
    'Gene': list(correlation_list3.keys()),
    'Observed_Correlation': list(correlation_list3.values()),
    'P_Value': list(corrected_p_value_jad.values())
})

# Remove genes with NaN p-values
results_df1 = results_df1.dropna(subset=['P_Value'])

# Sort by p-value
results_df1 = results_df1.sort_values('P_Value')

# Number of tests
m1 = len(results_df1)

# Desired FDR level
alpha = 0.05

# Rank the p-values
results_df1['Rank'] = np.arange(1, m1+1)

# Calculate the BH critical values
results_df1['BH_Critical'] = results_df1['Rank'] / m1 * alpha

# Determine significance
results_df1['BH_Significant'] = results_df1['P_Value'] <= results_df1['BH_Critical']

# Find the largest p-value that is significant
significant_results1 = results_df1[results_df1['BH_Significant']]

if not significant_results1.empty:
    max_rank = significant_results1['Rank'].max()
    # All p-values up to max_rank are significant
    results_df1['BH_Final_Significant'] = results_df1['Rank'] <= max_rank
else:
    results_df1['BH_Final_Significant'] = False

# Display significant results
significant_genes1 = results_df1[results_df1['BH_Final_Significant']]

significant_correlated_genes1 = significant_genes1[significant_genes1['Observed_Correlation'] > 0.2]

/var/folders/d8/pdrt51hx2jb17vf6k28_x6mh0000gn/T/ipykernel_22291/1449637510.py:30: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/var/folders/d8/pdrt51hx2jb17vf6k28_x6mh0000gn/T/ipykernel_22291/1449637510.py:30: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/var/folders/d8/pdrt51hx2jb17vf6k28_x6mh0000gn/T/ipykernel_22291/1449637510.py:30: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

/var/folders/d8/pdrt51hx2jb17vf6k28_x

In [64]:
# import plotly.graph_objects as go
# # Define color based on p-value condition
# colors = ['blue' if p < 0.05 else 'red' for p in list(results_df1['P_Value'])]

# gene_names = [key for key in correlation_list3.keys() if correlation_list3[key] > 0.2]


# # Create the bar plot
# fig = go.Figure(go.Bar(
#     x=[a for a in list(results_df1['Observed_Correlation']) if a > 0.2],
#     y=gene_names,
#     orientation='h',  # Horizontal bar chart
#     marker=dict(color=colors),  # Color based on p-value threshold
# ))

# fig.add_shape(
#         # Line Horizontal
#         dict(
#             type="line",
#             x0=0.2,
#             y0=0,
#             x1=0.2,
#             y1=len(gene_names),
#             line=dict(
#                 color="black",
#                 width=3,
#                 dash="dash"
#             )
# ))

# # Update layout for better visualization
# fig.update_layout(
#     xaxis_title="Correlation Coefficient",
#     yaxis_title="Gene ID",
#     height=1200,  # Adjust height based on the number of genes to avoid squeezing
#     yaxis=dict(showticklabels=False),  # Hide y-axis tick labels (gene names still appear)
#     font=dict(size=20, color = 'black', family = 'Latex'),
#     showlegend=False
# )

# fig.show()


In [59]:
len(p_value_list3)

137

In [52]:
len([x for x in p_value_list3.values() if x < 0.05]), len(significant_genes_corrected_5), len(significant_genes1)

(125, 109, 107)

In [53]:
len([x for x in p_value_list3.values() if x < 0.01]), len(significant_genes_corrected_1), len(significant_genes1)

(116, 102, 107)

In [55]:
# import pandas as pd
# species_number_dict = {}
# max_group_size_dict = {}
# num_group_dict = {}

# for gene, value in gene_data_dict.items():
#     data_f = pd.DataFrame({
#         'ens_abs_diff': np.sqrt(value['ens_abs_diff']),
#         'jsd_diff': np.sqrt(value['jsd_diff']),
#         'Species1': [x['ingroup1'] for x in value['species_names']],
#         'Species2': [x['ingroup2'] for x in value['species_names']],
#         'Species3': [x['outgroup'] for x in value['species_names']]
#     })

#     data_long = pd.melt(
#         data_f,
#         id_vars=['ens_abs_diff', 'jsd_diff'],
#         value_vars=['Species1', 'Species2', 'Species3'],
#         var_name='Species_Position',
#         value_name='Species'
#     )
#     data_long['ens_abs_diff'] = data_long['ens_abs_diff']
#     data_long['jsd_diff'] = data_long['jsd_diff']
#     data_long['Species'] = data_long['Species'].astype(str)
#     data_long['Species'] = data_long['Species'].astype('category')

#     num_groups = len(set(data_long['Species']))
#     species_number_dict[gene] = len(set(data_long['Species']))
#     num_group_dict[gene] = num_groups
#     max_group_size = max(data_long.groupby('Species').size())
#     max_group_size_dict[gene] = max_group_size
    
# correlation_list5 = {}
# p_value_list5 = {}
# for gene, lists in gene_data_dict.items():
#     jad_list, ens_list = remove_outliers_iqr(lists['jsd_ratio'], lists['ens_log_ratio'])

#     #Add the correlation factor in the list
#     cor, p_value = scipy.stats.spearmanr(jad_list, ens_list)
#     correlation_list5[gene] = cor
#     p_value_list5[gene] = p_value 

# # Step 1: Correct p-values using the group size
# corrected_p_value_jad = {gene: p_value_list5[gene]*max_group_size_dict[gene] for gene in gene_data_dict.keys()}

# significant_genes_corrected_5 = [gene for gene in gene_data_dict.keys() if corrected_p_value_jad[gene] < 0.05]
# significant_genes_corrected_1 = [gene for gene in gene_data_dict.keys() if corrected_p_value_jad[gene] < 0.01]

# significant_genes_correlation_dict_5 = {gene: correlation_list5[gene] for gene in significant_genes_corrected_5}
# significant_genes_correlation_dict_1 = {gene: correlation_list5[gene] for gene in significant_genes_corrected_1}

# # Step 2: Apply Benjamini-Hochberg procedure
# # Create a DataFrame with genes and p-values
# results_df1 = pd.DataFrame({
#     'Gene': list(correlation_list5.keys()),
#     'Observed_Correlation': list(correlation_list5.values()),
#     'P_Value': list(corrected_p_value_jad.values())
# })

# # Remove genes with NaN p-values
# results_df1 = results_df1.dropna(subset=['P_Value'])

# # Sort by p-value
# results_df1 = results_df1.sort_values('P_Value')

# # Number of tests
# m1 = len(results_df1)

# # Desired FDR level
# alpha = 0.05

# # Rank the p-values
# results_df1['Rank'] = np.arange(1, m1+1)

# # Calculate the BH critical values
# results_df1['BH_Critical'] = results_df1['Rank'] / m1 * alpha

# # Determine significance
# results_df1['BH_Significant'] = results_df1['P_Value'] <= results_df1['BH_Critical']

# # Find the largest p-value that is significant
# significant_results1 = results_df1[results_df1['BH_Significant']]

# if not significant_results1.empty:
#     max_rank = significant_results1['Rank'].max()
#     # All p-values up to max_rank are significant
#     results_df1['BH_Final_Significant'] = results_df1['Rank'] <= max_rank
# else:
#     results_df1['BH_Final_Significant'] = False

# # Display significant results
# significant_genes1 = results_df1[results_df1['BH_Final_Significant']]

# significant_correlated_genes1 = significant_genes1[significant_genes1['Observed_Correlation'] > 0.2]

In [53]:
# gene_names = list(results_df1['Gene'])
# # Create the bar chart
# fig = go.Figure(go.Bar(
#     x=list(results_df1['Observed_Correlation']),
#     y=gene_names,
#     orientation='h',  # Horizontal bar chart
#     marker=dict(color=list(results_df1['P_Value']), coloraxis="coloraxis")  # Color based on the correlation factor
# ))
# fig.add_shape(
#     type="line",
#     x0=0.2, y0=0, x1=0.2, y1=len(gene_names),
#     line=dict(color="yellow", width=3, dash="dashdot"),
# )


# # Update layout for better visualization
# fig.update_layout(
#     xaxis_title="Correlation Coefficient",
#     yaxis_title="Gene ID",
#     coloraxis=dict(colorscale='Viridis'),  # Red for higher, blue for lower values
#     height=1500  # Adjust height based on the number of genes to avoid squeezing
# )

# fig.show()

In [57]:
correlation_list_significant = {gene:[correlation_list3[gene]] for gene in corrected_p_value_jad.keys() if corrected_p_value_jad[gene] < 0.05}

In [63]:
import plotly.express as px

# Data for histogram
values3 = list(correlation_list3.values())
custom_colorscale = ['#F4A300', '#c73d47']

# Create the histogram with density normalization
fig2 = px.histogram(
    values3,
    labels={'x': 'Correlation Coefficient', 'y': 'Density'},
    title=None,
    color_discrete_sequence=['#a7b8d8'],  # Set the color to a shade of orange
)   

# Update layout for presentation
fig2.update_layout(
    template='plotly_white',
    margin=dict(l=50, r=50, t=50, b=10),  # Adjust margins for a balanced look
    autosize=True,
    yaxis_title='<b>Count</b>',  # Explicit y-axis title
    xaxis_title=r'$\text{Spearman } \hat{\rho}$',  # Explicit x-axis title
    yaxis_title_font=dict(size=22),  # Adjust y-axis font size
    xaxis_title_font=dict(size=22),  # Adjust x-axis font size
    font=dict(size=20, color = 'black', family = 'Arial'),  # General font size for labels and titles
    width=800,  # Set figure width (optional for better control)
    height=400,  # Set figure height (optional for better control)
    showlegend=False  # Remove the legend
)

fig2.add_shape(
    type="line",
    x0=0.2, y0=0, x1=0.2, y1=15,
    line=dict(color="#c73d47", width=4, dash="dashdot"),
)

# Set transparency level and add a solid line around each bar
fig2.update_traces(
    opacity=1,  # Set the transparency (0 = fully transparent, 1 = fully opaque)
    marker_line_color='black',  # Color of the line around each bar
    marker_line_width=1.5,  # Width of the line around each bar
   xbins=dict(size=0.05)
)

fig2.update_xaxes(range=[-0.15, 0.9])


fig2.show()


fig2.write_image('correlation_coefficient.pdf')


In [62]:
# Data for histogram
values3 = list(correlation_list3.values())
custom_colorscale = ['#F4A300', '#c73d47']

# Create the histogram with density normalization
fig2 = px.box(
    values3,
    labels={'x': 'Correlation Coefficient', 'y': 'Density'},
    title=None,
    color_discrete_sequence=['#a7b8d8'],  # Set the color to a shade of orange
    orientation='h'
)   

# Update layout for presentation
fig2.update_layout(
    template='plotly_white',
    margin=dict(l=50, r=50, t=10, b=50),  # Adjust margins for a balanced look
    autosize=True,
    yaxis_title=None,  # Explicit y-axis title
    xaxis_title=r'$\text{Spearman } \hat{\rho}$',  # Explicit x-axis title
    yaxis_title_font=dict(size=22),  # Adjust y-axis font size
    xaxis_title_font=dict(size=22),  # Adjust x-axis font size
    font=dict(size=20, color = 'black', family = 'Arial'),  # General font size for labels and titles
    width=800,  # Set figure width (optional for better control)
    height=300,  # Set figure height (optional for better control)
    showlegend=False  # Remove the legend
)

fig2.add_shape(
    type="line",
    x0=0.2, y0=-0.5, x1=0.2, y1=0.5,
    line=dict(color="#c73d47", width=4, dash="dashdot"),
)

fig2.update_xaxes(
    showticklabels=True,
    showgrid=True,
    gridcolor='black',
    gridwidth=1,
    zeroline=True,
    zerolinecolor='black',
    zerolinewidth=1,
    range=[-0.15, 0.9],
    
)


# # Set transparency level and add a solid line around each bar
# fig2.update_traces(
#     opacity=1,  # Set the transparency (0 = fully transparent, 1 = fully opaque)
#     marker_line_color='black',  # Color of the line around each bar
#     marker_line_width=1.5  # Width of the line around each bar
# )

fig2.update_xaxes(range=[-0.15, 0.9])
fig2.write_image('correlation_coefficient_box.pdf')
fig2.show()

In [60]:
import pandas as pd
import plotly.express as px

# Custom color scale for categories
custom_colorscale = {
    'Pre-correction': '#fff4d3',  
    'Post-dependency correction': '#98c4ce', 
    'Post-dependency and multiple testing correction': '#e3edf7', 
}

# Create DataFrame
df = pd.DataFrame({
    "Category": ["Pre-correction", "Post-dependency correction", "Post-dependency and multiple testing correction"] * 2,
    "Significance Level": [0.01] * 3 + [0.05] * 3,
    "Significant Proportion": [125/137*100, 109/137*100, 107/137*100, 116/137*100, 102/137*100, 107/137*100],
    "Label": ["125/137", "109/137", "107/137", "116/137", "102/137", "107/136"]
})

# Code to create grouped bar chart using Plotly
fig = px.bar(
    df,
    x="Significance Level",
    y="Significant Proportion",
    color="Category",
    barmode="group",
    title=None,
    color_discrete_map=custom_colorscale,
    opacity=1,
    text="Label"  # Add text labels for each bar
)

fig.update_traces(
    textposition="outside",  # Place text outside the bars for better readability
    width=0.007,  # Adjust the width of the bars
    marker_line_color='black',  # Add a black line around the bars
    marker_line_width=2  # Set the width of the line around the bars
)

# Update layout for better formatting
fig.update_layout(
    template='plotly_white',
    margin=dict(l=50, r=50, t=5, b=50),
    autosize=True,
    yaxis_title='<b>Significant Correlation % </b>',
    xaxis_title='<b>Significance Level (α)</b>',
    font=dict(size=20, color='black', family='Arial'),
    width=600,
    height=395,
    showlegend=False,
    bargap=0.3,
    bargroupgap=0.1,
    legend=dict(
        title=None,
        font = dict(size=13),
        orientation="h",
        yanchor="top",
        y=-0.15,
        xanchor="center",
        x=0.5
    ),

)

# Set text position to be inside the bars for readability
fig.update_traces(textposition="outside")

fig.show()

# fig.write_image('/Users/gulugulu/repos/PuningAnalysis/results/figures/significant_proportion.pdf')


In [59]:
121/130, 102/130, 101/130, 113/130, 99/130, 99/130

(0.9307692307692308,
 0.7846153846153846,
 0.7769230769230769,
 0.8692307692307693,
 0.7615384615384615,
 0.7615384615384615)

## Mixed linear model with random effect

In [60]:
# Example structure of your data
import pandas as pd
import statsmodels.formula.api as smf

def get_smf_mixedlm_result(gene, gene_data_dict):
    # Step 1: Get the data for the gene
    value = gene_data_dict[gene]
    data_f = pd.DataFrame({
        'ens_abs_diff': np.sqrt(value['ens_abs_diff']),
        'jsd_diff': np.sqrt(value['jsd_diff']),
        'Species1': [x['ingroup1'] for x in value['species_names']],
        'Species2': [x['ingroup2'] for x in value['species_names']],
        'Species3': [x['outgroup'] for x in value['species_names']]
    })

    data_long = pd.melt(
        data_f,
        id_vars=['ens_abs_diff', 'jsd_diff'],
        value_vars=['Species1', 'Species2', 'Species3'],
        var_name='Species_Position',
        value_name='Species'
    )

    # Step 3: Adjust variables
    data_long['ens_abs_diff'] = data_long['ens_abs_diff'] / 3
    data_long['jsd_diff'] = data_long['jsd_diff'] / 3

    # Step 4: Convert species identifiers to strings and factors
    data_long['Species'] = data_long['Species'].astype(str)
    data_long['Species'] = data_long['Species'].astype('category')

    model = smf.mixedlm('ens_abs_diff ~ jsd_diff', data=data_long, groups=data_long['Species'])
    result = model.fit()

    var_random = result.cov_re.iloc[0, 0]

    # Fixed effects variance
    # Calculate variance of the linear predictor (fixed effects)
    fixed_effects = result.fe_params
    X = result.model.exog
    var_fixed = np.var(np.dot(X, fixed_effects))

    # Residual variance
    var_residual = result.scale

    # Marginal R-squared (fixed effects only)
    R_m2 = var_fixed / (var_fixed + var_random + var_residual)

    # Conditional R-squared (fixed + random effects)
    R_c2 = (var_fixed + var_random) / (var_fixed + var_random + var_residual)

    return result, R_m2, R_c2

In [61]:
# Example structure of your data
import pandas as pd
import statsmodels.formula.api as smf

def get_smf_ols_result(gene, gene_data_dict):
    # Step 1: Get the data for the gene
    value = gene_data_dict[gene]
    data_f = pd.DataFrame({
        'ens_abs_diff': np.sqrt(value['ens_abs_diff']),
        'jsd_diff': np.sqrt(value['jsd_diff']),
        'Species1': [x['ingroup1'] for x in value['species_names']],
        'Species2': [x['ingroup2'] for x in value['species_names']],
        'Species3': [x['outgroup'] for x in value['species_names']]
    })

    data_long = pd.melt(
        data_f,
        id_vars=['ens_abs_diff', 'jsd_diff'],
        value_vars=['Species1', 'Species2', 'Species3'],
        var_name='Species_Position',
        value_name='Species'
    )

    reduced_model = smf.ols('ens_abs_diff ~ jsd_diff', data=data_long)
    result = reduced_model.fit()

    return result

In [62]:
multiple_linear_regression_data = {'gene': {}, 'p_value':{}, 'marginal_r^2': {}, 'conditional_r^2': {}}
for gene, value in gene_data_dict.items():
    data_f = pd.DataFrame({
        'ens_abs_diff': np.sqrt(value['ens_abs_diff']),
        'jsd_diff': np.sqrt(value['jsd_diff']),
        'Species1': [x['ingroup1'] for x in value['species_names']],
        'Species2': [x['ingroup2'] for x in value['species_names']],
        'Species3': [x['outgroup'] for x in value['species_names']]
    })

    data_long = pd.melt(
        data_f,
        id_vars=['ens_abs_diff', 'jsd_diff'],
        value_vars=['Species1', 'Species2', 'Species3'],
        var_name='Species_Position',
        value_name='Species'
    )

    # Step 3: Adjust variables
    data_long['ens_abs_diff'] = data_long['ens_abs_diff'] / 3
    data_long['jsd_diff'] = data_long['jsd_diff'] / 3

    # Step 4: Convert species identifiers to strings and factors
    data_long['Species'] = data_long['Species'].astype(str)
    data_long['Species'] = data_long['Species'].astype('category')

    model = smf.mixedlm('ens_abs_diff ~ jsd_diff', data=data_long, groups=data_long['Species'])
    result = model.fit()

        # Random effects variance
    var_random = result.cov_re.iloc[0, 0]

    # Fixed effects variance
    # Calculate variance of the linear predictor (fixed effects)
    fixed_effects = result.fe_params
    X = result.model.exog
    var_fixed = np.var(np.dot(X, fixed_effects))

    # Residual variance
    var_residual = result.scale

    # Marginal R-squared (fixed effects only)
    R_m2 = var_fixed / (var_fixed + var_random + var_residual)

    # Conditional R-squared (fixed + random effects)
    R_c2 = (var_fixed + var_random) / (var_fixed + var_random + var_residual)

    multiple_linear_regression_data['gene'][gene] = gene
    multiple_linear_regression_data['p_value'][gene] = result.pvalues['jsd_diff']
    multiple_linear_regression_data['marginal_r^2'][gene] = R_m2
    multiple_linear_regression_data['conditional_r^2'][gene] = R_c2


/Users/gulugulu/opt/anaconda3/envs/c312/lib/python3.12/site-packages/statsmodels/regression/mixed_linear_model.py:2237: ConvergenceWarning:

The MLE may be on the boundary of the parameter space.

/Users/gulugulu/opt/anaconda3/envs/c312/lib/python3.12/site-packages/statsmodels/regression/mixed_linear_model.py:2237: ConvergenceWarning:

The MLE may be on the boundary of the parameter space.

/Users/gulugulu/opt/anaconda3/envs/c312/lib/python3.12/site-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/Users/gulugulu/opt/anaconda3/envs/c312/lib/python3.12/site-packages/statsmodels/regression/mixed_linear_model.py:2200: ConvergenceWarning:

Retrying MixedLM optimization with lbfgs

/Users/gulugulu/opt/anaconda3/envs/c312/lib/python3.12/site-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/Users/gulugulu/opt/anaconda3/envs/c312

KeyboardInterrupt: 

In [48]:
multiple_linear_regression_data['r^2_difference'] = {gene: multiple_linear_regression_data['conditional_r^2'][gene] - multiple_linear_regression_data['marginal_r^2'][gene] for gene in multiple_linear_regression_data['gene']}

In [49]:
r_squared_data = pd.DataFrame(multiple_linear_regression_data)

In [ ]:

import plotly.graph_objects as go
import pandas as pd
# Create horizontal Bar traces for Marginal R² and Conditional R²
trace_marginal = go.Bar(
    x=r_squared_data['marginal_r^2'],  # Swap the y-values to x for horizontal bars
    y=r_squared_data['gene'],  # Use gene names as y-axis values
    name='Marginal R²',
    marker_color='#6fba4f',
    hovertext=r_squared_data['gene'],  # Show gene names on hover
    hoverinfo='text+x',  # Display gene name and R² value on hover
    orientation='h'  # Set orientation to horizontal
)

trace_conditional = go.Bar(
    x=r_squared_data['conditional_r^2'],  # Swap the y-values to x for horizontal bars
    y=r_squared_data['gene'],  # Use gene names as y-axis values
    name='Conditional R²',
    marker_color='#e87cf4',
    hovertext=r_squared_data['gene'],  # Show gene names on hover
    hoverinfo='text+x',  # Display gene name and R² value on hover
    orientation='h'  # Set orientation to horizontal
)

# Combine the traces
data_traces = [trace_marginal, trace_conditional]

# Define the layout
layout = go.Layout(
    title=None,
    xaxis=dict(
        title='<b>R² Value<b>',  # X-axis now represents R² values
        tickfont=dict(size=14),
        range=[0, 1],  # Assuming R² ranges between 0 and 1
        titlefont=dict(size=20, color='black'),  # Adjust font size and color
    ),
    yaxis=dict(
        title='<b>Gene</b>',  # Y-axis now represents genes
        showticklabels = False,  # Hide tick labels
        titlefont=dict(size =20, color='black'),  # Adjust font size and color
    ),
    barmode='group',  # Side-by-side bars
    bargap=0.15,      # Gap between groups of bars
    bargroupgap=0.1,  # Gap between bars within a group
    legend=dict(
        x=0.85,
        y=1,
        bgcolor='rgba(255,255,255,0)',
        bordercolor='rgba(255,255,255,0)'
    ),
    template='plotly_white',
    margin=dict(l=60, r=30, t=80, b=60),
    height=1300  # Adjust height based on the number of genes to avoid squeezing
)

# Create the figure
fig = go.Figure(data=data_traces, layout=layout)

# Display the plot
fig.show()

# fig.write_image('/Users/gulugulu/repos/PuningAnalysis/results/figures/marginal_and_conditionalr_squared.pdf')


## Scatter plot for each gene

In [51]:


def plot_gene_data(gene_data_dict, xcol, ycol):
    keys = list(gene_data_dict.keys())
    rows = int(len(keys) ** 0.5) + 1  # Calculate the number of rows for subplots
    cols = (len(keys) + rows - 1) // rows  # Calculate the number of columns

    fig = make_subplots(rows=rows, cols=cols, subplot_titles=[f'{key}' for key in keys])
    
    # Populate subplots
    for index, key in enumerate(keys, start=1):
        gene_data = gene_data_dict[key]
        x_value, y_value = remove_outliers_iqr(gene_data[xcol], gene_data[ycol])

        row = (index - 1) // cols + 1
        col = (index - 1) % cols + 1
        
        fig.add_trace(
            go.Scatter(
                x=x_value,
                y=y_value,
                mode='markers',
                name=f'{key}'
            ),
            row=row,
            col=col
        )
        
        # Adding a trend line
        fig.add_trace(
            go.Scatter(
                x=x_value,
                y=np.poly1d(np.polyfit(x_value, y_value, 1))(x_value),
                mode='lines',
                name=f'Trend {key}',
                line=dict(color='red')
            ),
            row=row,
            col=col
        )
        
        # Update axis properties
        fig.update_xaxes(title_text=xcol if row == rows else "", row=row, col=col)
        fig.update_yaxes(title_text=ycol if col == 1 else "", row=row, col=col)
    
    fig.update_layout(
        height=300 * rows,  # Set a reasonable height based on the number of rows
        width=300 * cols,   # Set a reasonable width based on the number of columns
        showlegend=False
    )
    
    return fig

In [52]:
# Usage example
fig = plot_gene_data(gene_data_dict, 'jsd_diff', 'ens_abs_diff')

fig.update_layout(
title_text="Scatter Plots of JAD Difference vs. ENS Difference",)
fig.show()

In [134]:
path = '/Users/gulugulu/Desktop/honours/data_local_2/triples_model_fitting_550_threshold/ENSG00000065613'

gene_name = path.split('/')[-1]

triads_data_path = os.path.join(path, 'triples_info_dict.json')
triads_info = load_json_data(triads_data_path)
ens_ingroup_list = []
ingroup_jsd_list = []
for identifier, info in triads_info.items():
    triads_info_value = info['triples_info_small_tree']
    triads_names = info['triples_species_names']
    ingroup_jsd = triads_info_value['ingroup_jsd']
    ens_dict = triads_info_value['ens']
    ens_ingroup = abs(ens_dict[triads_names['ingroup1']] - ens_dict[triads_names['ingroup2']])
    ens_ingroup_list.append(ens_ingroup)
    ingroup_jsd_list.append(ingroup_jsd)


ens_ingroup_list2, ingroup_jsd_list2 = remove_outliers_iqr(ens_ingroup_list, ingroup_jsd_list)


In [135]:
indices_ens_diff2 = list(range(1, len(ens_ingroup_list2) + 1))
indices_ingroup_jsd2 = list(range(1, len(ingroup_jsd_list2) + 1))

list_pair = []
for i in range(len(indices_ens_diff2)):
    jsd_value, ens = ingroup_jsd_list2[i], ens_ingroup_list2[i]
    list_pair.append((jsd_value, ens))



In [136]:
# Create the scatter plot
fig1 = go.Figure()

# # Add ENS Differences scatter plot
# fig1.add_trace(go.Scatter(
#     x=indices_ingroup_jsd2, y=sorted(ens_ingroup_list2), mode='markers',
#     marker=dict(size=4), name='ENS Differences'))

fig1.add_trace(go.Scatter(
    x=indices_ens_diff2, y=sorted(ens_ingroup_list2), mode='markers',
    marker=dict(size=4, color = '#6fba4f'), name='Ingroup JSD'))


# Update layout for clear visualization
fig1.update_layout(
    title=gene_name,
    xaxis_title='<b>Index</b>',
    yaxis_title='<b>ENS difference</b>',
    showlegend=False,
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    width=600,
    height=300,    
)

fig1.show()
fig1.write_image(f'/Users/gulugulu/repos/PuningAnalysis/results/figures/ENS_diff_{gene_name}_full.pdf')

In [137]:
# Create the scatter plot
fig1 = go.Figure()

# # Add ENS Differences scatter plot
# fig1.add_trace(go.Scatter(
#     x=indices_ingroup_jsd2, y=sorted(ens_ingroup_list2), mode='markers',
#     marker=dict(size=4), name='ENS Differences'))

fig1.add_trace(go.Scatter(
    x=indices_ingroup_jsd2, y=sorted(ingroup_jsd_list2), mode='markers',
    marker=dict(size=4, color = "#f0a3f8"), name='Ingroup JSD'))


# Update layout for clear visualization
fig1.update_layout(
    title=gene_name,
    xaxis_title='<b>Index</b>',
    yaxis_title='<b>Ingroup JSD</b>',
    showlegend=False,
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    width=600,
    height=300,    
)

fig1.show()
fig1.write_image(f'/Users/gulugulu/repos/PuningAnalysis/results/figures/ingroup_jsd_{gene_name}_full.pdf')

In [ ]:
# Create the scatter plot
fig1 = go.Figure()

# # Add ENS Differences scatter plot
# fig1.add_trace(go.Scatter(
#     x=indices_ingroup_jsd2, y=sorted(ens_ingroup_list2), mode='markers',
#     marker=dict(size=4), name='ENS Differences'))

fig1.add_trace(go.Scatter(
    x=indices_ingroup_jsd2, y=sorted(ens_ingroup_list2), mode='markers',
    marker=dict(size=4), name='Ingroup JSD'))


# Update layout for clear visualization
fig1.update_layout(
    title=None,
    xaxis_title='<b>Ingroup JSD</b>',
    yaxis_title='<b>Values</b>',
    showlegend=False,
    template='plotly_white',
    margin=dict(l=20, r=20, t=20, b=20),
    width=600,
    height=700
    
)

fig1.show()

In [58]:
import numpy as np
import plotly.graph_objects as go
from scipy.stats import uniform

def qq_plot_uniform(data):
    """
    Creates a QQ plot of the provided data against a uniform distribution using Plotly.

    Args:
    data (array-like): The dataset to plot.
    a (float): The lower bound of the uniform distribution (default 0).
    b (float): The upper bound of the uniform distribution (default 1).
    """
    
    # Scale data for the specified uniform range
    data = np.array(data)
    data.sort()  # Sort the data for plotting

    a = min(data)
    b = max(data)
    scaled_data = (data - a) / (b - a)

    # Calculate quantiles
    n = len(data)
    theoretical_quantiles = uniform.ppf(np.arange(1, n + 1) / (n + 1))

    # Create a QQ plot
    fig = go.Figure()

    # Adding scatter plot for QQ plot
    fig.add_trace(go.Scatter(x=theoretical_quantiles, y=scaled_data, mode='markers',
                             name=None,
                             marker=dict(color='blue')))

    # Add line of perfect fit
    fig.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode='lines',
                             name=None,
                             line=dict(color='red', dash='dash')))

    # Update layout
    fig.update_layout(
                      xaxis_title='Uniform Quantiles',
                      yaxis_title='Sample Quantiles',
                      width=600, height=600)

    # Show plot
    fig.show()

In [59]:
path_jsd = '/Users/gulugulu/Desktop/honours/data_local_2/triples_550_threshold/ENSG00000009307/jsd_bins.json'
with open(path_jsd, 'r') as file:
    jsd_bins = json.load(file)

In [60]:
path_ens = '/Users/gulugulu/Desktop/honours/data_local_2/triples_550_threshold/ENSG00000009307/ens_diff_bins.json'
with open(path_ens, 'r') as file:
    ens_bins = json.load(file)

In [61]:
jsd_binning_list = [value['triples_info_big_tree']['jsd_dict']['Ingroup_JSD'] for value in jsd_bins['bins'].values() if value is not None]
ens_binning_list = [value['triples_info_big_tree']['ens_difference'] for value in ens_bins['bins'].values() if value is not None]

In [90]:
qq_plot_uniform(ens_binning_list)

In [63]:
# Create the scatter plot
fig1 = go.Figure()

# Add ENS Differences scatter plot
fig1.add_trace(go.Scatter(
    x=np.sqrt(x_values), y=sorted(y_values), mode='markers',
    marker=dict(size=4), name='ENS Differences'))



# Update layout for clear visualization
fig1.update_layout(
    title='Uniform distirbution of each property',
    xaxis_title='Index',
    yaxis_title='Values',
    showlegend=True,
    
)

fig1.show()

In [64]:
import numpy as np
import scipy.stats as stats

def permute_test_correlation(x, y, n_permutations=10000):
    # Calculate the actual correlation
    actual_corr, _ = stats.pearsonr(x, y)
    
    # To hold the permuted correlations
    permuted_corrs = []

    original_y = np.copy(y)
    
    # Permutation test
    for _ in range(n_permutations):
        # Shuffle one of the lists
        np.random.shuffle(y)
        # Compute the correlation of the permuted data
        perm_corr, _ = stats.pearsonr(x, y)
        permuted_corrs.append(perm_corr)

        y[:] = original_y
    
    # Compute p-value: proportion of permuted correlations as extreme as the actual one
    p_value = np.sum(np.abs(permuted_corrs) >= np.abs(actual_corr)) / n_permutations
    
    return actual_corr, p_value, permuted_corrs





# Factor impacts the correlation analysis

Sequence composition analysis

In [65]:
import os
import json

def extract_internal_root_distribution(base_path):
    gene_dirs = [d for d in os.listdir(base_path) if os.path.isdir(os.path.join(base_path, d))]
    all_data = {}

    for gene_id in gene_dirs:
        gene_path = os.path.join(base_path, gene_id)
        internal_root_distribution = {}

        # Files to process
        path = os.path.join(gene_path, 'triples_info_dict.json')
        if os.path.exists(path):
            with open(path, 'r') as f:
                data = json.load(f)
                for identifier, content in data.items():
                    if content: 
                        triads_info = content['triples_info_small_tree']
                        nuc_freqs_dict = triads_info['nuc_freqs_dict']
                        internal_root_info = nuc_freqs_dict["internal_node"]
                        internal_root_distribution[str(identifier)] = internal_root_info

        all_data[gene_id] = internal_root_distribution

    return all_data

# Base directory containing all gene ID folders
base_path = '/Users/gulugulu/Desktop/honours/data_local_2/triples_model_fitting_550_threshold'
result = extract_internal_root_distribution(base_path)

information_dict = {}
for gene_id, distirbutions_info in result.items():
    information_dict[gene_id] = {}
    for identifier, distirbution in distirbutions_info.items():
        information_dict[gene_id][identifier] = calculate_information(distirbution)

# # Optionally, save this data to a file
# output_file = os.path.join(base_path, 'internal_root_distributions.json')
# with open(output_file, 'w') as f:
#     json.dump(result, f, indent=4)

In [66]:
average_information_dict = {}
for gene, informations in information_dict.items():
    average_information_dict[gene] = np.average(list(informations.values()))

In [67]:
average_distribution_dir = {}
for gene, distributions in result.items():
    average_distribution_dir[gene] = np.mean(np.array(list(distributions.values())), axis=0)

In [68]:
average_info_dict = {gene: calculate_information(distribution) for gene, distribution in average_distribution_dir.items()}

In [69]:
import plotly.express as px
corr_list_sorted = {gene: correlation_list3[gene] for gene in average_info_dict.keys()}
fig = px.scatter(x = average_info_dict.values(), y = corr_list_sorted.values(), labels={'x':'Information', 'y':'Correlation Coefficient'}, title= None)
# Update layout with labels and title
fig.update_layout(
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    autosize=True,
    yaxis_title_font={'size': 20},  
    xaxis_title_font={'size': 20}, 
    width=None 
)
fig.show()

Genome length analysis

In [70]:
from cogent3 import open_data_store, get_app
load_json_app = get_app("load_json")

big_tree_res_dir = '/Users/gulugulu/Desktop/honours/data_local_2/whole_gene_model_fitting_550_threshold'

def extract_big_tree_info(base_path):
    ens_info_dict = {}
    result_input_dstore = open_data_store(base_path, suffix='json', mode='r')
    for path in result_input_dstore:
        trace_back_nodes = {}
        gene_name = path.unique_id.split('.')[0]
        print(gene_name)
        res_lf = load_json_app(path).lf
        tip_names = res_lf.tree.get_tip_names()
        for speices in tip_names:
            trace_back_path = []
            for tree in res_lf.tree.get_connecting_edges('root', speices):
                internal_root = tree.get_node_names()[0]
                trace_back_path.append(internal_root)
            trace_back_nodes[speices] = trace_back_path
        ens_dict = {species: np.sum([res_lf.get_ens_tree().to_rich_dict()['edge_attributes'][n]['length'] for n in trace_back_nodes[species][1:]]) for species in res_lf.tree.get_tip_names()}
        ens_info_dict[gene_name] = ens_dict
        print('finished')

    return ens_info_dict

In [71]:
# ens_big_tree_info_dir = extract_big_tree_info(big_tree_res_dir)

In [72]:
# ens_big_tree_info_average_ens_dir = {gene: np.mean(list(ens_info.values())) for gene, ens_info in ens_big_tree_info_dir.items()}
# ens_big_tree_info_average_ens_dir_filtered = {gene: ens_big_tree_info_average_ens_dir[gene] for gene in ens_big_tree_info_average_ens_dir.keys() if ens_big_tree_info_average_ens_dir[gene] < 2 }
# corr_list_length_sorted = {gene: correlation_list3[gene] for gene in ens_big_tree_info_average_ens_dir_filtered.keys()}

In [73]:
# import plotly.express as px

# fig = px.scatter(x = ens_big_tree_info_average_ens_dir_filtered.values(), y = corr_list_length_sorted.values(), labels={'x':'Average Length', 'y':'Correlation Coefficient'}, trendline="ols",title= None)
# # Update layout with labels and title
# fig.update_layout(
#     template='plotly_white',
#     margin=dict(l=20, r=20, t=50, b=20),
#     autosize=True,
#     yaxis_title_font={'size': 20},  
#     xaxis_title_font={'size': 20}, 
#     width=None 
# )
# fig.show()

In [74]:
# del ens_big_tree_info_average_ens_dir['ENSG00000134250']
# del ens_big_tree_info_average_ens_dir['ENSG00000110237']
# del ens_big_tree_info_average_ens_dir['ENSG00000126705']
# del ens_big_tree_info_average_ens_dir['ENSG00000214655']


In [75]:
# import plotly.express as px
# corr_list_length_sorted = {gene: correlation_list3[gene] for gene in ens_big_tree_info_average_ens_dir.keys()}
# fig = px.scatter(x = ens_big_tree_info_average_ens_dir.values(), y = corr_list_length_sorted.values(), labels={'x':'Average Length', 'y':'Correlation Coefficient'}, trendline="ols", title= None)
# # Update layout with labels and title
# fig.update_layout(
#     template='plotly_white',
#     margin=dict(l=20, r=20, t=50, b=20),
#     autosize=True,
#     yaxis_title_font={'size': 20},  
#     xaxis_title_font={'size': 20}, 
#     width=None 
# )
# fig.show()

In [76]:
# def extract_ens(base_path):
#     gene_dirs = [d for d in os.listdir(base_path) if os.path.isdir(os.path.join(base_path, d))]
#     all_data = {}

#     for gene_id in gene_dirs:
#         gene_path = os.path.join(base_path, gene_id)
#         ens_dict_values = {}

#         # Files to process
#         path = os.path.join(gene_path, 'triples_info_dict_new.json')
#         if os.path.exists(path):
#             with open(path, 'r') as f:
#                 data = json.load(f)
#                 for identifier, content in data.items():
#                     if content: 
#                         triads_info = content['triples_info_small_tree']
#                         ens_dict = triads_info['ens']

#                         ens_values = list(ens_dict.values())
#                         internal_edge_length = ens_values[3]
#                         ens_dict_values[str(identifier)] = [a + internal_edge_length for a in ens_values[0:2]]
#         all_data[gene_id] = ens_dict_values

#     return all_data

In [77]:
# ens_info_dir = extract_ens(base_dir)

# ens_info_average_small_tree_dir = {}
# for gene, ens_info in ens_info_dir.items():
#     ens_info_average_small_tree_dir[gene] = np.mean(np.array(list(ens_info.values())), axis=0)
# overall_ens = {gene: np.mean(ens_info_average_small_tree_dir[gene]) for gene in ens_info_average_small_tree_dir.keys()}

In [78]:
# import plotly.express as px
# corr_list_length_sorted = {gene: correlation_list3[gene] for gene in overall_ens.keys()}
# fig = px.scatter(x = overall_ens.values(), y = corr_list_length_sorted.values(), labels={'x':'Average in-group branch Length', 'y':'Correlation Coefficient'}, trendline="ols", title= None)
# # Update layout with labels and title
# fig.update_layout(
#     template='plotly_white',
#     margin=dict(l=20, r=20, t=50, b=20),
#     autosize=True,
#     yaxis_title_font={'size': 20},  
#     xaxis_title_font={'size': 20}, 
#     width=None 
# )
# fig.show()